In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)

from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, classification_report, accuracy_score

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from lightgbm import LGBMClassifier
import lightgbm as lgb

In [2]:
def evaluate_model(model, X_test, y_test):
    """
    Evaluate a classification model given the model and test data.
    
    Parameters:
        model: Trained classification model.
        X_test (pd.DataFrame or np.array): Test features.
        y_test (array-like): True labels.
        
    Prints:
        - AUC (if probabilities or decision scores are available)
        - Classification report (precision, recall, f1-score)
    """
    # Predict classes
    y_pred = model.predict(X_test)

    # Try to get predicted probabilities for positive class
    if hasattr(model, "predict_proba"):
        y_proba = model.predict_proba(X_test)[:, 1]
    elif hasattr(model, "decision_function"):
        y_proba = model.decision_function(X_test)
    else:
        y_proba = None
    
    # Classification report
    print("Classification Report:")
    print(classification_report(y_test, y_pred))
    
    # AUC score if probabilities or decision function available
    if y_proba is not None:
        auc = roc_auc_score(y_test, y_proba)
        print(f"AUC: {auc:.4f}")
    else:
        print("AUC cannot be calculated because no probability or decision function is available.")


In [3]:
df = pd.read_csv('../data/processed/data.csv')
df.sort_values(by='Date', ascending=True)
df.drop(['Date'], axis=1, inplace=True)
model_features = df.columns.to_list()
target = 'RainTomorrow'

X = df.drop(target, axis=1)
y = df[target]

# Train Test Split

In [4]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=False)

# Baseline model (LR)

In [5]:
lr = LogisticRegression()
#lr.fit(X_train, y_train)
#evaluate_model(lr, X_test, y_test)

# Random Forest model

In [6]:
rf = RandomForestClassifier()
#rf.fit(X_train, y_train)
#evaluate_model(rf, X_test, y_test)

# KNN

In [7]:
knn = KNeighborsClassifier()
#knn.fit(X_train, y_train)
#evaluate_model(knn, X_test, y_test)

# LightGBM

In [8]:
lgbm = LGBMClassifier()
lgbm.fit(X_train, y_train)
evaluate_model(lgbm, X_test, y_test)

[LightGBM] [Info] Number of positive: 24195, number of negative: 85604
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005543 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1782
[LightGBM] [Info] Number of data points in the train set: 109799, number of used features: 23
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.220357 -> initscore=-1.263586
[LightGBM] [Info] Start training from score -1.263586
Classification Report:
              precision    recall  f1-score   support

           0       0.89      0.95      0.92     22105
           1       0.71      0.54      0.61      5345

    accuracy                           0.87     27450
   macro avg       0.80      0.74      0.76     27450
weighted avg       0.86      0.87      0.86     27450

AUC: 0.8866


# LightGBM w/ Optuna

In [9]:
import optuna
import lightgbm as lgb
import numpy as np
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import roc_auc_score


cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

from lightgbm import LGBMClassifier

def objective(trial):
    params = {
        'objective': 'binary',
        'boosting_type': 'gbdt',
        'learning_rate': trial.suggest_float("learning_rate", 0.01, 0.2, log=True),
        'num_leaves': trial.suggest_int("num_leaves", 20, 150),
        'max_depth': trial.suggest_int("max_depth", 4, 12),
        'min_child_samples': trial.suggest_int("min_child_samples", 10, 60),  # equivalente a min_data_in_leaf
        'feature_fraction': trial.suggest_float("feature_fraction", 0.6, 1.0),
        'bagging_fraction': trial.suggest_float("bagging_fraction", 0.6, 1.0),
        'bagging_freq': trial.suggest_int("bagging_freq", 1, 10),
        'reg_alpha': trial.suggest_float("reg_alpha", 0.0001, 10.0, log=True),
        'reg_lambda': trial.suggest_float("reg_lambda", 0.0001, 10.0, log=True),
        'min_split_gain': trial.suggest_float("min_split_gain", 0.0, 1.0),
        'random_state': 42,
        'n_estimators': trial.suggest_int("n_estimators", 100, 1000)
    }

    auc_scores = []
    
    for train_idx, valid_idx in cv.split(X, y):
        X_train, X_valid = X.iloc[train_idx], X.iloc[valid_idx]
        y_train, y_valid = y.iloc[train_idx], y.iloc[valid_idx]

        model = LGBMClassifier(**params, early_stopping_rounds=50)
        model.fit(
            X_train,
            y_train,
            eval_set=[(X_valid, y_valid)],
            eval_metric='auc',
        )

        y_pred = model.predict_proba(X_valid)[:, 1]
        auc = roc_auc_score(y_valid, y_pred)
        auc_scores.append(auc)

    return np.mean(auc_scores)


# Run the optimization
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=75)

# Results
print("Best AUC:", study.best_value)
print("Best parameters:", study.best_params)


/Users/robertogarces/miniforge3/envs/aus_rain/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2025-05-25 09:40:36,757] A new study created in memory with name: no-name-4458964f-74e1-4b7b-bec9-595d9c8c1659


[LightGBM] [Warning] early_stopping_round is set=50, early_stopping_rounds=50 will be ignored. Current value: early_stopping_round=50
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] bagging_fraction is set=0.8895524178500327, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8895524178500327
[LightGBM] [Warning] feature_fraction is set=0.9286839613311271, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9286839613311271
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.9286839613311271, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9286839613311271
[LightGBM] [Warning] bagging_fraction is set=0.8895524178500327, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8895524178500327
[LightGBM] [Info] Number of positive: 23632, num

[I 2025-05-25 09:40:46,834] Trial 0 finished with value: 0.8885206798907369 and parameters: {'learning_rate': 0.17483000930581677, 'num_leaves': 48, 'max_depth': 8, 'min_child_samples': 31, 'feature_fraction': 0.9286839613311271, 'bagging_fraction': 0.8895524178500327, 'bagging_freq': 5, 'reg_alpha': 0.017181186377074914, 'reg_lambda': 0.5092302170156471, 'min_split_gain': 0.49069558523471557, 'n_estimators': 881}. Best is trial 0 with value: 0.8885206798907369.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
Early stopping, best iteration is:
[199]	valid_0's auc: 0.888091	valid_0's binary_logloss: 0.324071
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] bagging_fraction is set=0.8895524178500327, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8895524178500327
[LightGBM] [Warning] feature_fraction is set=0.9286839613311271, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9286839613311271
[LightGBM] [Warning] early_stopping_round is set=50, early_stopping_rounds=50 will be ignored. Current value: early_stopping_round=50
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] bagging_fraction is set=0.9789994131638775, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9789994131638775
[LightGBM] [Warning] featur

[I 2025-05-25 09:41:12,709] Trial 1 finished with value: 0.8917295336703696 and parameters: {'learning_rate': 0.036596560729691696, 'num_leaves': 123, 'max_depth': 8, 'min_child_samples': 37, 'feature_fraction': 0.9200120315758599, 'bagging_fraction': 0.9789994131638775, 'bagging_freq': 1, 'reg_alpha': 0.06740223856385798, 'reg_lambda': 0.0005347797317851329, 'min_split_gain': 0.06232974475424513, 'n_estimators': 559}. Best is trial 1 with value: 0.8917295336703696.


...

[LightGBM] [Warning] early_stopping_round is set=50, early_stopping_rounds=50 will be ignored. Current value: early_stopping_round=50
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] bagging_fraction is set=0.7125919830040267, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7125919830040267
[LightGBM] [Warning] feature_fraction is set=0.8103038110640255, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8103038110640255
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.8103038110640255, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8103038110640255
[LightGBM] [Warning] bagging_fraction is set=0.7125919830040267, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7125919830040267
[LightGBM] [Info] Number of positive: 23632, num

[I 2025-05-25 10:39:06,256] Trial 73 finished with value: 0.8934647930413678 and parameters: {'learning_rate': 0.03589518568249631, 'num_leaves': 121, 'max_depth': 12, 'min_child_samples': 33, 'feature_fraction': 0.8103038110640255, 'bagging_fraction': 0.7125919830040267, 'bagging_freq': 5, 'reg_alpha': 0.03518913128796446, 'reg_lambda': 3.621937980463938, 'min_split_gain': 0.004192355251060709, 'n_estimators': 870}. Best is trial 68 with value: 0.8940791884256394.


[LightGBM] [Warning] early_stopping_round is set=50, early_stopping_rounds=50 will be ignored. Current value: early_stopping_round=50
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] bagging_fraction is set=0.6854799479591778, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6854799479591778
[LightGBM] [Warning] feature_fraction is set=0.7100459471469992, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7100459471469992
[LightGBM] [Warning] bagging_freq is set=6, subsample_freq=0 will be ignored. Current value: bagging_freq=6
[LightGBM] [Warning] feature_fraction is set=0.7100459471469992, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7100459471469992
[LightGBM] [Warning] bagging_fraction is set=0.6854799479591778, subsample=1.0 will be ignored. Current value: bagging_fraction=0.6854799479591778
[LightGBM] [Info] Number of positive: 23632, num

[I 2025-05-25 10:39:57,679] Trial 74 finished with value: 0.8939361283883244 and parameters: {'learning_rate': 0.02878086894755253, 'num_leaves': 137, 'max_depth': 12, 'min_child_samples': 55, 'feature_fraction': 0.7100459471469992, 'bagging_fraction': 0.6854799479591778, 'bagging_freq': 6, 'reg_alpha': 0.012147965720860502, 'reg_lambda': 5.134630527946008, 'min_split_gain': 0.16088012130031948, 'n_estimators': 916}. Best is trial 68 with value: 0.8940791884256394.


Best AUC: 0.8940791884256394
Best parameters: {'learning_rate': 0.024866257380641667, 'num_leaves': 127, 'max_depth': 11, 'min_child_samples': 55, 'feature_fraction': 0.8106418795364716, 'bagging_fraction': 0.8474018890040552, 'bagging_freq': 5, 'reg_alpha': 0.009772667510304865, 'reg_lambda': 6.144629955782155, 'min_split_gain': 0.16255786625919597, 'n_estimators': 930}


In [10]:
best_params = study.best_params
train_data = lgb.Dataset(X_train, label=y_train)

model = lgb.train(
    best_params,
    train_data,
)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003303 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1782
[LightGBM] [Info] Number of data points in the train set: 109799, number of used features: 23
[LightGBM] [Info] Start training from score 0.220357
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

In [11]:
y_pred_proba = model.predict(X_test)
y_pred = (y_pred_proba >= 0.5).astype(int)
print(classification_report(y_test, y_pred))
auc = roc_auc_score(y_test, y_pred_proba)
print(f"AUC: {auc:.4f}")

              precision    recall  f1-score   support

           0       0.89      0.95      0.92     22105
           1       0.72      0.52      0.60      5345

    accuracy                           0.87     27450
   macro avg       0.80      0.73      0.76     27450
weighted avg       0.86      0.87      0.86     27450

AUC: 0.8857
